# **Intro to SiS1 Labs**

The goal of the labs of Signal and Systems 1 is to gain knowledge on the course’s topics by solving a specific signal processing problem. By the end of the course, you should be able to imitate, by synthesis, the sound produced by a plucked string instrument using the knowledge acquired in the theory and seminar classes. This will be a cumulative process, in each lab new techniques will be applied in order to improve the synthesis. First let's show what we will achieve by the end of the course. For each lab we need to import some auxiliary functions needed to load the audio files and listen to them:


In [2]:
from util import load_audio, save_audio, plot_signals
from IPython.display import Audio

Matplotlib is building the font cache; this may take a moment.


**Reference signal**

Now let's load and listen to a reference signal like the one you will use:

In [6]:
reference, fs = load_audio('audio/reference.wav')
Audio(reference, rate=fs)

**Synthesis**

Now we can load and listen to a synthesised signal like the one you will obtain and that tries to imitate the reference signal. This is an audio signal created from scratch only using the knowledge gained during the course.

In [7]:
synthesis, fs = load_audio('audio/synthesis.wav')
Audio(synthesis, rate=fs)

---

## **Lab 1**
In this lab you will choose your reference sound to be used for all the labs and start imitating it with a single sinusoid.

## **Exercises**

**1. Choose a reference sound**

1.1. Find a recording of a single plucked string sound. Be creative, do not choose “guitar” by default, nor copy a sound from another group. You should use [Freesound](https://freesound.org/) to find the recordings (Freesound is a huge collaborative database of audio snippets released under Creative Commons licenses created and maintained by researchers of the Music Technology Group of the UPF). Try to find a sound with the best possible quality. The ideal sound format should be: uncompress (such as.wav, .aiff, but no .mp3), mono (one channel) and with a sampling rate of  44100Hz. The sound file should also contain a single note. You can start by downloading a sound from freesound and modify it with Audacity to the right format and content.

https://freesound.org/people/Jagadamba/sounds/253767/

1.2. Create a github repository and upload your edited audio file there:

1) Sing up to github using your UPF gmail account: https://github.com/

2) Create a repository called **sis1_groupX** where X is your group number: https://docs.github.com/en/get-started/quickstart/create-a-repo

3) Upload your edited audio file to the repository


1.3. Now you can clone your repository and access the audio file locally. Change the following code (user name and file name) to clone the repository and load the audio file.

In [ ]:
!git clone https://github.com/Alexjarne/sis1-group102.git
filepath = "./sis1-group102/labs/audio/audioSisLabs.wav"
ref, fs = load_audio(filepath)


Note that `load_audio` function returns two variables: the audio signal (as a one dimensional array of floating point numbers), and the sampling rate (as a integer number). Now we can plot the audio signal:

In [16]:
plot_signals(ref, fs)

You can use the zoom in tool to see more details.

You can also use Audio widget to listen the audio signal:

In [17]:
Audio(ref, rate=fs)




---



**2. Measure the signal period and fundamental frequency**

2.1. Measure the period length, in seconds, and the fundamental frequency, in Hz, of the sound you choose. You can use Audacity to measure the period by zooming into a stable portion of the sound. Then compute its inverse to find the fundamental frequency. Find the closest note (note name) of the measured frequency (use google).

I zoomed into a steady part of the recording and measured the period and frequency. The period is approximately 0.002676 seconds and the fundamental frequency is approximately 373.73 hertz. The closest equal-tempered note with A4 at 440 hertz is F sharp 4 also called G flat 4 and it is about 17 cents sharp.

2.2. Calculate the period from the frequency value using Python:


In [19]:
f0 = 373.728813559322  # your measured frequency from 2.1 (Hz)
T = 1.0 / f0
print(f"T = {T:.6f} s ({T*1e3:.3f} ms)")


T = 0.002676 s (2.676 ms)


2.3. Plot three periods of the signal using the `plot_signals` function and selecting `t_start` and `t_end` arguments accordingly. Try to get the first periods of the audio signal but avoiding the attack section.

In [24]:
from util import load_audio, plot_signals

FILEPATH = "./sis1-group102/labs/audio/audioSisLabs.wav"
x, fs = load_audio(FILEPATH)

t_start = 0.14
t_end   = t_start + 3*T

plot_signals([x], sr=fs, t_start=t_start, t_end=t_end, name=["reference"])


2.4. Measure the period of the signal manually by identifying the begining and ending of a periodic cycle. Note that when you hover the mouse over one of the points in the plot, you can see the time and amplitude values. For instance, you can check the cross by zero.

After zooming into a steady segment and checking the distance between consecutive upward zero crossings, the measured period is approximately 2.65 milliseconds. This corresponds to a measured frequency of approximately 390.6 hertz.

2.5. Do the measured (2.4) and theoretical (2.2) periods coincide? If not, explain why.

The measured and theoretical values are very close but not identical. From question 2.2 the theoretical period is approximately 2.676 milliseconds and the theoretical frequency is approximately 373.7 hertz. The absolute difference between periods is about 0.034 milliseconds which is about 1.27 percent of the theoretical period. The absolute difference between frequencies is about 4.81 hertz which is about 1.29 percent of the theoretical frequency. The small mismatch is explained by the window you choose for measurement, the sound not being a perfectly pure sinusoid because it has harmonics and a decaying envelope, finite sampling effects, and small manual readout inaccuracies.



---



**3. Generating a sinusoid**

3.1. Create a sinusoid of the same duration than the reference signal and same frequency than the fundamental frequency. Plot it along with the audio signal of the reference recording. Plot the same time segment that 2.3. Note that the sampling rate should be the same for both signals. Try to find the values of Amplitude and initial Phase that make the two signal segments plotted to match as close as possible (do not attempt to imitate the whole signal). Matching the phase is a bit tricky.



In [53]:
import numpy as np

N = len(ref); t_all = np.arange(N)/fs; w = 2*np.pi*f0
ta, tb = t_start, t_end
m = (t_all >= ta) & (t_all <= tb)
tm = t_all[m]; xm = ref[m]
C = np.column_stack([np.cos(w*tm), np.sin(w*tm)])
a, b = np.linalg.lstsq(C, xm, rcond=None)[0]
A_fit = 0.5
phi_fit = 5.28


synth = A_fit * np.cos(w*t_all + phi_fit)

plot_signals([ref, synth], sr=fs, t_start=t_start, t_end=t_end, name=["AudioSisLab", "synth"])

print(f"A={A_fit:.4f}, phi={phi_fit:.4f} rad, f0={f0:.2f} Hz")


A=0.5000, phi=5.2800 rad, f0=373.73 Hz


3.2. What are the main differences between the two signals.

The two signals are quite different. The reference is not a pure tone: it contains harmonics and a small amount of noise, so its waveform looks sharp and irregular. Its amplitude also decays over time and there are slight cycle-to-cycle variations (from the instrument and the recording). In contrast, the synthesized signal is a single sinusoid: it has a smooth shape, constant amplitude, and perfectly regular cycles. The phase can be aligned only within the short window we fitted; outside that window the real signal drifts slightly, so the curves separate. 


3.3. Listen to the synthesized signal usign the Audio widget. Sounds natural?

In [ ]:
Audio(synth, rate=fs)
#doesnt sound natural but when you play both together it sound similar. 




3.4. Save the synthesized signal using the 'save_audio` function:

In [60]:
from util import save_audio
import numpy as np, os

out_path = "./sis1-group102/labs/audio/synthesis2.wav"
os.makedirs(os.path.dirname(out_path), exist_ok=True)

s_out = np.clip(synth, -1.0, 1.0).astype(np.float32)  # mono 1-D is fine
save_audio(out_path, s_out, fs)
print("Saved:", out_path)



Saved: ./sis1-group102/labs/audio/synthesis2.wav
